In [ ]:
import sys

sys.path.append("..")
from omegaconf import OmegaConf
from sgm.util import instantiate_from_config

config = OmegaConf.load(
    "/vol/paramonos2/projects/antoni/code/Personal/generative-models/configs/example_training/svd_interpolation.yaml"
)
print(config)
config["model"]["params"]["ckpt_path"] = "../checkpoints/svd.safetensors"
video_model = instantiate_from_config(config.model)

In [ ]:
model.model.learned_mask.sum((1, 2))

In [ ]:
from torchvision.io import read_video
import torch

video_path = "/data2/Datasets/HDTF/cropped_videos_original/WRA_BobbySchilling_001.mp4"
resolution = 512
device = torch.device("cuda")

video, audio, info = read_video(video_path, pts_unit="sec", output_format="TCHW")

from torchvision.transforms import Resize

resize = Resize((resolution, resolution))
video = resize(video)
print(video.shape)

In [ ]:
audio_path = "/data2/Datasets/HDTF/audio/WRA_BobbySchilling_001_whisper_emb.pt"
audio = torch.load(audio_path)
print(audio.shape)

In [ ]:
video.min(), video.max()

In [ ]:
model.first_stage_model.encoder

In [ ]:
model = model.to(device)
encoded = model.conditioner.embedders[3]((video[:2].to(device).float() / 255.0) * 2 - 1)

In [ ]:
from PIL import Image
import numpy as np

video_model.to(device)
# decoded = video_model.decode_first_stage(encoded[:, 4:])
decoded = video_model.decode_first_stage(encoded)
img = Image.fromarray(np.uint8((decoded[0].clip(-1, 1).cpu().numpy().transpose(1, 2, 0) + 1) * 255 / 2))
display(img)

In [ ]:
from safetensors.torch import load_file

latent_path = "/vol/bitbucket/abigata/00190_video_512_latent.safetensors"

latent = load_file(latent_path)
latent["latents"].shape

In [ ]:
decoded = video_model.decode_first_stage(latent["latents"][:1].to("cpu"))

In [ ]:
from PIL import Image
import numpy as np

img = Image.fromarray(np.uint8((decoded[0].clip(-1, 1).cpu().numpy().transpose(1, 2, 0) + 1) * 255 / 2))
display(img)

In [ ]:
import sys

sys.path.append("..")
from omegaconf import OmegaConf
from sgm.util import instantiate_from_config

config = OmegaConf.load(
    "/vol/paramonos2/projects/antoni/code/Personal/generative-models/configs/inference/sd_2_1.yaml"
)
print(config)
config["model"]["params"][
    "ckpt_path"
] = "/vol/paramonos2/projects/antoni/code/Personal/generative-models/checkpoints/v2-1_512-ema-pruned.safetensors"
model = instantiate_from_config(config.model)

In [ ]:
from torchvision.io import read_video
import torch

video_path = "/data2/Datasets/HDTF/cropped_videos_original/WRA_BobbySchilling_001.mp4"
resolution = 512
device = torch.device("cuda:4")

video, audio, info = read_video(video_path, pts_unit="sec", output_format="TCHW")

from torchvision.transforms import Resize

resize = Resize((resolution, resolution))
video = resize(video)
print(video.shape)

In [ ]:
model.to(device)
encoded = model.encode_first_stage((video[:2].to(device).float() / 255.0) * 2 - 1)

In [ ]:
# decoded = model.decode_first_stage(encoded)
decoded = model.decode_first_stage(latent["latents"][:1].to(device))

In [ ]:
from PIL import Image
import numpy as np

img = Image.fromarray(np.uint8((decoded[0].clip(-1, 1).cpu().numpy().transpose(1, 2, 0) + 1) * 255 / 2))
display(img)

In [1]:
from transformers import Wav2Vec2Processor, Wav2Vec2ForCTC

# load model and tokenizer
processor = Wav2Vec2Processor.from_pretrained("facebook/wav2vec2-base-960h", cache_dir="/vol/bitbucket/abigata/.cache")
model = Wav2Vec2ForCTC.from_pretrained("facebook/wav2vec2-base-960h", cache_dir="/vol/bitbucket/abigata/.cache")

/vol/paramonos2/projects/antoni/miniconda3/envs/svd/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
Some weights of the model checkpoint at facebook/wav2vec2-base-960h were not used when initializing Wav2Vec2ForCTC: ['wav2vec2.encoder.pos_conv_embed.conv.weight_g', 'wav2vec2.encoder.pos_conv_embed.conv.weight_v']
- This IS expected if you are initializing Wav2Vec2ForCTC from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing Wav2Vec2ForCTC from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of Wav2Vec2ForCTC were 

In [2]:
import torch
from einops import rearrange

# load audio
audio_path = "/data2/Datasets/HDTF/audio/WRA_CandiceMiller0_000_wav2vec2_emb.pt"
audio_emb = torch.load(audio_path)
print(audio_emb.shape)

logits = model.lm_head(rearrange(audio_emb, "f d c -> () (f d) c", d=2))

torch.Size([3000, 2, 768])


In [3]:
logits.shape

torch.Size([1, 6000, 32])

In [4]:
# Transcribe

predicted_ids = torch.argmax(logits, dim=-1).squeeze()

# transcribe
transcription = processor.decode(predicted_ids)
transcription

"LLED IN SAN FRANCISCO BY AN UNDOCUMENTED IMIGRANT NAMED FRANCISCO SANCHS IT WAS A VERY TRAGIC INCIDENT THAT CUT SHORT THE INNOCENT HIFE OF A YOUNG WOMAN WITH A VERY BRIGHT FUTURE AND IN THE WAKE OF THIS INCIDENT MANY ARE ASKING WHY SANCHEZ A SEVEN TIME FELIN WHO HAS BEEN DEPORTED FROM THE UNITED STATES FIVE TIMES SINCE NINETEEN NINETY FIVE WAS EVEN FREE TO ROME THE STREETS AND THE ANSWER IS INSAN FRANCISCO WHAT IS KNOWN AS A SANCTUARY CITY LAW ENFORCEMENT OFFICIAS ARE PROHIBITED FROM ENFORCING FEDERAL EMIGRATION POLICIES WHICH IN THIS CASE ALSO INCLUDED IGNORING AN EMIGRATION AN CUSTOMS INFORCEMENT REQUEST TO DETAIN SANCHEZ PRIOR TO THE SHOOTING I BELIEVE THAT IT IS HYPOCRITICAL OF THESE CITIES TO DEFY FEDERAL EMIGRATION LAWS AND THEN TO TURN AROUND AND ASK FOR FEDERAL LAW ENFORCEMENT GRANTS INCLUDING GRANT SPECIFICALLY INTENDED TO HELP WITH EFFORTS TO APPREHEND UNDOCUMENTED CRIMINALS LIKE SANCHES IT ISN'T RIGHT IT ISN'T LEGAL AND IT CREATES POTENTIALLY DANGEROUS SITUATIONS FOR OUR CI

In [ ]:
from einops import rearrange

audio_reshaped = rearrange(audio.mean(0)[:640000], "(f s) -> f s", s=320)
audio_reshaped.shape

In [ ]:
processed = processor(audio=audio_reshaped, sampling_rate=sr, return_tensors="pt", padding="longest").input_values

In [ ]:
processed.shape

In [11]:
import torch

normed_slice = (audio_resampled - audio_resampled.mean()) / torch.sqrt(audio_resampled.var() + 1e-7)

In [ ]:
normed_slice.shape

In [ ]:
model??

In [12]:
with torch.no_grad():
    outs = model(normed_slice, output_hidden_states=True)
    # hidden_states = model.wav2vec2(normed_slice)

In [17]:
outs.hidden_states[0].shape[1] / 2

749.5

In [ ]:
model.dropout(hidden_states[0])

In [ ]:
for h in outs.hidden_states:
    print(h.shape)

In [3]:
from torchvision.io import read_video
import torch

video_path = "/data2/Datasets/HDTF/cropped_videos_original/WRA_DaveCamp_000.mp4"
resolution = 512
device = torch.device("cuda:4")

video, audio, info = read_video(video_path, pts_unit="sec", output_format="TCHW")
video.shape

torch.Size([750, 3, 690, 690])

In [10]:
len_seconds_video = video.shape[0] / info["video_fps"]
len_seconds_audio = audio.shape[1] / info["audio_fps"]
print(len_seconds_video, len_seconds_audio)

import torchaudio

audio_resampled = torchaudio.transforms.Resample(info["audio_fps"], 16000)(audio.mean(0, keepdim=True))

len_resampled_audio = audio_resampled.shape[1] / 16000
len_resampled_audio

30.0 30.00018140589569


30.0001875

In [13]:
predicted_ids = torch.argmax(outs.logits, dim=-1).squeeze()

# transcribe
transcription = processor.decode(predicted_ids)
transcription

"RAL SIDE AND N IN TO SOME EXTENT THE STRUCTURE ON THE INTERNATIONAL SIDE WITH THE DEEMED REPATRIATION AND MOVING TO A TERRITORIAL SYSTEM BUT THERE ARE SIGNIFICANT DIFFERENCES I MEAN THIS PLAN ACTUALLY REALLY IS ADDRESSING THE CONCEPT OF DYNAMIC SCORING WHICH WAS A NEW THING WHEN I WORKED ON TAXTORFORM THEYRE REALLY TAKING FULL ADVANTAGE OF THAT WITH THE FULL EXPENSING FOR FIVE YEARS AND THE'RE GETTING THE CORPORATE RAPE DOWN LOWER AND THEY'RE MAKING IT PERMANENT SO I THINK IF THAT CAN HOLD THER'E SOME QUESTION WHETHER THIS SENTT WILL BE ABLE TO MEET ALL THOSE METRICS BUT AT LEAST IN THIS HOUSE VERSION IT IT'S GOT SOME SIMILAARY"

In [ ]:
"LLED IN SAN FRANCISCO BY AN UNDOCUMENTED IMIGRANT NAMED FRANCISCO SANCHS IT WAS A VERY TRAGIC INCIDENT THAT CUT SHORT THE INNOCENT HIFE OF A YOUNG WOMAN WITH A VERY BRIGHT FUTURE AND IN THE WAKE OF THIS INCIDENT MANY ARE ASKING WHY SANCHEZ A SEVEN TIME FELIN WHO HAS BEEN DEPORTED FROM THE UNITED STATES FIVE TIMES SINCE NINETEEN NINETY FIVE WAS EVEN FREE TO ROME THE STREETS AND THE ANSWER IS INSAN FRANCISCO WHAT IS KNOWN AS A SANCTUARY CITY LAW ENFORCEMENT OFFICIAS ARE PROHIBITED FROM ENFORCING FEDERAL EMIGRATION POLICIES WHICH IN THIS CASE ALSO INCLUDED IGNORING AN EMIGRATION AN CUSTOMS INFORCEMENT REQUEST TO DETAIN SANCHEZ PRIOR TO THE SHOOTING I BELIEVE THAT IT IS HYPOCRITICAL OF THESE CITIES TO DEFY FEDERAL EMIGRATION LAWS AND THEN TO TURN AROUND AND ASK FOR FEDERAL LAW ENFORCEMENT GRANTS INCLUDING GRANT SPECIFICALLY INTENDED TO HELP WITH EFFORTS TO APPREHEND UNDOCUMENTED CRIMINALS LIKE SANCHES IT ISN'T RIGHT IT ISN'T LEGAL AND IT CREATES POTENTIALLY DANGEROUS SITUATIONS FOR OUR CITIZENS AND SO TO DY THE HOUSE PASS LEGISLATION THAT BLOCK STATES AND MININCIPALITIES THAT BREAK THE LAW AND FAILED TO ENFORCE FEDERAL EMIGRATION LAWS FROM RECEIVING FEDERAL GRANTS INTENDED TO ASSIST THEM IN THESE EFFORTS CERTAIN ORGANIZATIONS HAVE IDENTIFIED AT LEAST TWO CITIES IN THE STATE OF MICHIGAN THAT HAVE PASSED RESOLUTIONS MAKING THEM SANCTUARY CITIES DETROIT AND AN ARBOR AND ALTHOUGH I'M NOT AWARE OF ANY SPECIFIC INCIDENTS IF THEY OR ANY OTHER SANCTUARY CITY RELY ON THESE FEDERAL GRANTS AND IF THEY THINK THIS PENALTY IS TOO HARSH THERE'S A VERY EASY SOLUTION OVER TURN YOUR POLICIES RESIND THESE RESOLUTIONS AND ENFORCE THE LAW I MUST NOTE THAT THE FEDERAL GOVERNMENT DOES NOT HAVE CLEAN HANDS IN THIS MATTER AS FEDERAL AGENCIES ARE ALSO RELEASING ILLEGAL IMIGRANTS UNDER THIS ADMINISTRATIONS MISGUIDED POLICIES HOWEVER THIS BILL WHICH STOP"

In [5]:
# Plot video
import moviepy.editor as mp

mp.VideoFileClip("/data2/Datasets/HDTF/cropped_videos_original/WRA_CandiceMiller0_000.mp4").subclip(
    0, 50
).ipython_display()

Moviepy - Building video __temp__.mp4.
MoviePy - Writing audio in __temp__TEMP_MPY_wvf_snd.mp3


MoviePy - Done.
Moviepy - Writing video __temp__.mp4



Moviepy - Done !
Moviepy - video ready __temp__.mp4


: 